# Metallicity Switchboard

In [53]:
import astropy.units as u
import astropy.constants as ac
from astropy.cosmology import FlatLambdaCDM
import numpy as np
import pandas as pd
import os
from os.path import expanduser
from astropy.table import Table
from glob import glob
from O3N2 import*
from SFR import*
from Distance import*
from Ha_Luminosity import*
from findR23 import*
from O3HB import*
from N2 import*

In [54]:
# gala is a data table of Final_galinfo.csv file which 
# is a subset of data from the galaxyinfo.xlsx data from CGM^2

pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 1000)

galaxy = pd.read_csv('../test/Final_galinfo.csv')

galaxy.to_numpy()   # This turns the DataFrame into a NumPy array.

# This 'for' loop will look for '-99' values and change them to 'NaN' values.

columns = ['NII_flux', 'SIIa_flux', 'Halpha_flux', 'OII_flux', 'Hbeta_flux', 'OIII_flux',
          'SIIb_flux']

for i in columns:
    n = 0
    while n < len(galaxy):
        
        if galaxy[i][n] == -99.0:
            galaxy[i][n] = np.nan
        n += 1    
        
        
galaxy[0:2]

/Users/josephbreneman/miniconda3/lib/python3.7/site-packages/ipykernel_launcher.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


specfile                       id      OBJECT  \
0  J022601.51+001532.5.fits  J022601.51+001532.5._03  J0226+0015   
1  J022602.41+001536.6.fits  J022602.41+001536.6._01  J0226+0015   

             cgm_name     gal_ra  gal_dec         z  OII_flux  OII_flux_sig  \
0  J0226+0015_271_194  36.506302  0.25904  0.352715       NaN         -99.0   
1  J0226+0015_272_181  36.510059  0.26017  0.297832       NaN         -99.0   

   OII_LQ    Hbeta_flux  Hbeta_flux_sig  Hbeta_LQ     OIII_flux  \
0   -99.0  2.130000e-17    2.440000e-18       1.0  2.250000e-17   
1   -99.0           NaN   -9.900000e+01     -99.0  2.190000e-17   

   OIII_flux_sig  OIII_LQ   Halpha_flux  Halpha_flux_sig  Halpha_LQ  \
0   1.760000e-18      1.0  3.120000e-17     2.470000e-18        1.0   
1   1.870000e-18      1.0  2.080000e-17     8.410000e-19        1.0   

       NII_flux  NII_flux_sig  NII_LQ     SIIa_flux  SIIa_flux_sig  SIIa_LQ  \
0  1.120000e-17  2.570000e-18     1.0  1.290000e-17   7.990000e-19      1.0   
1           NaN -9.900000e+01   -99.0           NaN  -9.900000e+01      2.0   

      SIIb_flux  SIIb_flux_sig  SIIb_LQ Comment  
0  1.760000e-18   1.140000e-18      1.0     NaN  
1           NaN  -9.900000e+01      2.0     NaN

## Calculate Distance

In [55]:
galaxy['Distance'] = Distance(galaxy['z'])

#galaxy

## Calculate Halpha and Hbeta Luminosity

In [56]:
galaxy['Ha_luminosity'] = Ha_luminosity(galaxy['Distance'],galaxy['Halpha_flux'])

Hbeta = 2.86*galaxy['Hbeta_flux']
galaxy['Hb_luminosity'] = Ha_luminosity(galaxy['Distance'],Hbeta)


#galaxy

## Calculate SFR

In [57]:
# Calculating SFR using Halpha luminosity
galaxy['SFR_Ha'] = SFR(galaxy['Ha_luminosity'])

# Calculating SFR using Hbeta luminosity, and then eliminating values (NaN) 
# that already have 'SFR_Ha' values not equal to NaN
sfr_b = SFR(galaxy['Hb_luminosity'])
nosfr_b = np.where(galaxy['SFR_Ha'] > 0.0)
sfr_b[nosfr_b] = np.nan
galaxy['SFR_Hb'] = sfr_b

#galaxy

In [58]:
print(len(sfr_b))
sfr_b[0]

782


nan

In [59]:
SFR_flags, Ha_index, Hb_index = SFR_switchboard(galaxy)

print(len(SFR_flags))

SFR_flags[0]

#galaxy['SFR_flag'] = SFR_flags

782


array(['Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha',
       'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha',
       'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha', 'Ha',
       'Ha'], dtype=object)

## Calculate 'O3HB'

In [60]:
galaxy['O3HB'] = O3HB(galaxy['OIII_flux'],galaxy['Hbeta_flux'])

#galaxy

## Calculate 'N2' 

In [62]:
galaxy['N2'] = N2(galaxy['NII_flux'],galaxy['Halpha_flux'])

#galaxy

## Calculate 'O3N2'

In [63]:
galaxy['O3N2'] = O3N2(galaxy)

#galaxy

## Calculate 'Z_O3N2L'

In [64]:
galaxy['Z_O3N2L'] = Z_O3N2L(galaxy)

#galaxy

#### -The 'O3N2' function only calculates metallicity if O3N2 < 1.9. There needs to be a function for calculating metallicity for O3N2 > 1.9.

In [65]:
np.where(galaxy['O3N2'] > 1.9)

(array([414]),)

-If 'O3N2' or 'O3HB' could not be calculated (NaN) and we only have N2 index then the equation for calculating 'Z_O3N2+' (when O3N2 > 1.9) can be used for calculating metallicity.

In [37]:
# This cell finds the N2 values that require metallicity calculations

n2_maybe = np.where((np.isnan(galaxy['O3HB']) & (np.isnan(galaxy['O3N2']))))

n2 = np.array(galaxy['N2'])
n2_yes = n2[n2_maybe]
np.where(n2_yes > 0.0)

/Users/josephbreneman/miniconda3/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in greater
  import sys


(array([  0,  42,  45,  46,  48,  54,  62,  65,  66,  74,  75,  76,  89,
         91,  92,  93,  95,  99, 145, 163, 181, 201, 202, 206, 207, 213,
        214, 219, 223, 233, 234, 236, 243]),)

## Mass and friends

In [38]:
# Steven's technique

# filepath for table containing stellar masses for all the galaxies that we've been working with:

home = expanduser('~')
path = os.path.join(home,'Dropbox','**','cgmsq_allsurveys_cgmsystable.fits')
massfilepath = glob(path, recursive=True)

# Extracts table from fits file and resolves various issues required to concatenate this new table (which Matt
# made at some point previously) with our new SFR info-containing table.

mass_and_friends = Table.read(massfilepath[-1])
mass_and_friends.remove_columns(['zRR', 'zRR_Err', 'spectype_rr'])
mass_and_friends = mass_and_friends.to_pandas()
mass_and_friends['id'] = mass_and_friends['id'].str.decode('utf-8')

# merges mass table with initial (SFR-containing) one:

galaxy = pd.merge(galaxy, mass_and_friends, on=['id'], how='right')

# sorting out some (more) naming conflicts:

galaxy.rename(columns={'z_x': 'z'}, inplace=True)


## Calculate R23

In [39]:
r23 = findR23(galaxy['OII_flux'],galaxy['OIII_flux'],galaxy['NII_flux'],galaxy['Halpha_flux'],
             galaxy['Hbeta_flux'],galaxy['mstars'])

/Users/josephbreneman/miniconda3/lib/python3.7/site-packages/pandas/core/series.py:679: RuntimeWarning: invalid value encountered in log10
  result = getattr(ufunc, method)(*inputs, **kwargs)


## Add columns for R23 metallicity

In [40]:
galaxy['Z_R23'] = r23[0]
galaxy['Z_R23_flag'] = r23[1]

galaxy

specfile_x                       id    OBJECT_x  \
0    J022601.51+001532.5.fits  J022601.51+001532.5._03  J0226+0015   
1    J022602.41+001536.6.fits  J022602.41+001536.6._01  J0226+0015   
2    J022606.98+001451.4.fits  J022606.98+001451.4._02  J0226+0015   
3    J022607.08+001612.7.fits  J022607.08+001612.7._01  J0226+0015   
4    J022608.02+001427.2.fits  J022608.02+001427.2._03  J0226+0015   
5    J022609.11+001513.1.fits  J022609.11+001513.1._01  J0226+0015   
6    J022610.26+001603.7.fits  J022610.26+001603.7._01  J0226+0015   
7    J022610.44+001514.0.fits  J022610.44+001514.0._03  J0226+0015   
8    J022611.06+001323.6.fits  J022611.06+001323.6._02  J0226+0015   
9    J022611.40+001341.3.fits  J022611.40+001341.3._01  J0226+0015   
10   J022612.15+001357.5.fits  J022612.15+001357.5._03  J0226+0015   
11   J022612.18+001407.3.fits  J022612.18+001407.3._01  J0226+0015   
12   J022612.18+001506.0.fits  J022612.18+001506.0._01  J0226+0015   
13   J022613.33+001358.7.fits  J022613.33+001358.7._01  J0226+0015   
14   J022614.39+001620.4.fits  J022614.39+001620.4._02  J0226+0015   
15   J022614.58+001351.4.fits  J022614.58+001351.4._03  J0226+0015   
16   J022616.82+001624.7.fits  J022616.82+001624.7._01  J0226+0015   
17   J022617.54+001834.5.fits  J022617.54+001834.5._01  J0226+0015   
18   J022617.99+001447.5.fits  J022617.99+001447.5._02  J0226+0015   
19   J022619.99+001435.3.fits  J022619.99+001435.3._02  J0226+0015   
20   J022622.00+001642.3.fits  J022622.00+001642.3._01  J0226+0015   
21   J080852.41+461747.5.fits  J080852.41+461747.5._03  J0809+4619   
22   J080859.67+462048.0.fits  J080859.67+462048.0._04  J0809+4619   
23   J080901.07+462153.4.fits  J080901.07+462153.4._03  J0809+4619   
24   J080901.51+462029.7.fits  J080901.51+462029.7._02  J0809+4619   
25   J080901.64+461903.3.fits  J080901.64+461903.3._01  J0809+4619   
26   J080903.95+462000.0.fits  J080903.95+462000.0._03  J0809+4619   
27   J080903.96+461952.5.fits  J080903.96+461952.5._02  J0809+4619   
28   J080903.97+461911.9.fits  J080903.97+461911.9._04  J0809+4619   
29   J080904.33+461854.9.fits  J080904.33+461854.9._01  J0809+4619   
30   J080905.28+461944.8.fits  J080905.28+461944.8._01  J0809+4619   
31   J080906.99+461859.1.fits  J080906.99+461859.1._03  J0809+4619   
32   J080907.49+461857.9.fits  J080907.49+461857.9._01  J0809+4619   
33   J080908.10+462053.4.fits  J080908.10+462053.4._04  J0809+4619   
34   J080909.03+462012.7.fits  J080909.03+462012.7._01  J0809+4619   
35   J080910.70+461648.6.fits  J080910.70+461648.6._03  J0809+4619   
36   J080912.38+461901.2.fits  J080912.38+461901.2._02  J0809+4619   
37   J080912.98+461846.3.fits  J080912.98+461846.3._02  J0809+4619   
38   J080913.42+462053.3.fits  J080913.42+462053.3._01  J0809+4619   
39   J080913.54+461954.1.fits  J080913.54+461954.1._02  J0809+4619   
40   J080913.68+462032.5.fits  J080913.68+462032.5._04  J0809+4619   
41   J080914.29+461822.0.fits  J080914.29+461822.0._01  J0809+4619   
42   J080914.36+462015.3.fits  J080914.36+462015.3._03  J0809+4619   
43   J080914.57+461655.7.fits  J080914.57+461655.7._04  J0809+4619   
44   J080916.16+462034.8.fits  J080916.16+462034.8._02  J0809+4619   
45   J080917.09+462018.0.fits  J080917.09+462018.0._02  J0809+4619   
46   J080918.23+462003.8.fits  J080918.23+462003.8._01  J0809+4619   
47   J080918.25+461934.8.fits  J080918.25+461934.8._02  J0809+4619   
48   J080918.30+461849.1.fits  J080918.30+461849.1._03  J0809+4619   
49   J080918.56+462004.3.fits  J080918.56+462004.3._03  J0809+4619   
50   J080919.08+461822.7.fits  J080919.08+461822.7._01  J0809+4619   
51   J080920.17+461921.0.fits  J080920.17+461921.0._03  J0809+4619   
52   J080922.68+461807.1.fits  J080922.68+461807.1._01  J0809+4619   
53   J080922.73+462045.6.fits  J080922.73+462045.6._02  J0809+4619   
54   J080924.29+461813.9.fits  J080924.29+461813.9._02  J0809+4619   
55   J080924.99+461958.6.fits  J080924.99+461958.6._03  J0809+4619   
56   J084340.92+411951.6.fits

In [41]:
# Defining the 'Z_flag' column

z_flag = np.array((len(galaxy))*[0])  

# Flagging metallicity calculated with O3N2
one = np.where(galaxy['Z_O3N2L'] > 0.0) 
z_flag[one] = 1

#two = requires N2 index metallicity calculations

# Flagging metallicity calculated with R23
three = np.where(galaxy['Z_R23'] > 0.0)
z_flag[three] = 3

galaxy['Z_Flag'] = z_flag

#galaxy

-Save to .csv